In [ ]:
import pandas as pd
import requests
import json
import os
import io
import py7zr
from google.transit import gtfs_realtime_pb2
import tempfile
from datetime import datetime
from dotenv import load_dotenv

load_dotenv()


In [ ]:
api_GTS_RT_KEY = os.getenv("API_GTFS_RT_KEY")
api_koda_key = os.getenv("API_KODA_KEY")
api_RT_national = os.getenv("API_GTFS_STATIC")

host_api = "https://api.koda.trafiklab.se/KoDa/api/v2"
base_path = "/gtfs-rt"
location_path = "/sl"
type_path = "/TripUpdates"
api_url = host_api + base_path + location_path + type_path

params = {
    "date": "2025-04-09", 
    "key": api_koda_key
}

In [3]:
#api_url_full = "https://api.koda.trafiklab.se/KoDa/api/v2/gtfs-rt/sl/TripUpdates?date=2025-11-03&key=MY_KODA_API_KEY"
r = requests.get(f"{api_url}", params=params, timeout=20)

print(r)
print("---"*3)
print(len(r.content))
print("---"*3)
print("Status:", r.status_code)
print("Content-Type:", r.headers.get("Content-Type"))
print("Content-Encoding:", r.headers.get("Content-Encoding"))
print("Début (bytes):", r.content[:8])

# ne contiens pas les 30j précédents sinon erreur

<Response [200]>
---------
72638308
---------
Status: 200
Content-Type: application/x-7z-compressed
Content-Encoding: None
Début (bytes): b"7z\xbc\xaf'\x1c\x00\x04"


In [4]:
archive_bytes = io.BytesIO(r.content)

with py7zr.SevenZipFile(archive_bytes, mode="r") as z:
    names = z.getnames()

# 1) Essayer d'abord les extensions classiques
candidates = [n for n in names if n.lower().endswith((".pb"))] # autres format possible mais non trouvé ".pbf", ".bin", ".protobuf"

# 2) Si pas d'extension, on détecte les "vrais fichiers" :
if not candidates:
    name_set = set(names)
    candidates = []
    for n in names:
        # si "n/<quelquechose>" existe, alors n est un dossier/prefixe
        is_prefix = any(other.startswith(n + "/") for other in names)
        if not is_prefix:
            candidates.append(n)

print("Total entrées:", len(names))
print("Candidats fichiers:", len(candidates))
print("Exemples candidats:", candidates[:10])


Total entrées: 6088
Candidats fichiers: 6059
Exemples candidats: ['sl/TripUpdates/2025/04/09/00/sl-tripupdates-2025-04-08T23-59-40Z.pb', 'sl/TripUpdates/2025/04/09/00/sl-tripupdates-2025-04-08T23-59-54Z.pb', 'sl/TripUpdates/2025/04/09/00/sl-tripupdates-2025-04-09T00-00-08Z.pb', 'sl/TripUpdates/2025/04/09/00/sl-tripupdates-2025-04-09T00-00-22Z.pb', 'sl/TripUpdates/2025/04/09/00/sl-tripupdates-2025-04-09T00-00-36Z.pb', 'sl/TripUpdates/2025/04/09/00/sl-tripupdates-2025-04-09T00-00-50Z.pb', 'sl/TripUpdates/2025/04/09/00/sl-tripupdates-2025-04-09T00-01-04Z.pb', 'sl/TripUpdates/2025/04/09/00/sl-tripupdates-2025-04-09T00-01-18Z.pb', 'sl/TripUpdates/2025/04/09/00/sl-tripupdates-2025-04-09T00-01-32Z.pb', 'sl/TripUpdates/2025/04/09/00/sl-tripupdates-2025-04-09T00-01-46Z.pb']


In [5]:
target = candidates[2300]
print("Fichier choisi:", target)

# Dossier temporaire
tmpdir = tempfile.mkdtemp(prefix="koda_")

archive_bytes = io.BytesIO(r.content)

with py7zr.SevenZipFile(archive_bytes, mode="r") as z:
    # Extraire seulement le fichier target
    z.extract(path=tmpdir, targets=[target])

# Chemin du fichier extrait
extracted_path = os.path.join(tmpdir, target)
print("Extrait vers:", extracted_path)
print("Existe ?", os.path.exists(extracted_path))

# Lire le .pb et parser
with open(extracted_path, "rb") as f:
    raw = f.read()

print("Taille brute extraite:", len(raw), "bytes")

feed = gtfs_realtime_pb2.FeedMessage()
feed.ParseFromString(raw)

print("✅ Entités GTFS-RT:", len(feed.entity))

Fichier choisi: sl/TripUpdates/2025/04/09/09/sl-tripupdates-2025-04-09T09-06-09Z.pb
Extrait vers: /var/folders/xs/9pw_49kx273dmym0qk_0l_s00000gn/T/koda_hbm70_s8/sl/TripUpdates/2025/04/09/09/sl-tripupdates-2025-04-09T09-06-09Z.pb
Existe ? True
Taille brute extraite: 1115124 bytes
✅ Entités GTFS-RT: 1312


In [6]:
shown = 0
print(len(feed.entity))
for e in feed.entity:
    print(e)

1312
id: "14010516766425338"
trip_update {
  trip {
    trip_id: "14010000664756938"
    start_date: "20250409"
    schedule_relationship: SCHEDULED
  }
  vehicle {
    id: "9031001004505106"
  }
  stop_time_update {
    stop_sequence: 71
    stop_id: "9022001060014001"
    arrival {
      delay: 120
      time: 1744181810
      uncertainty: 0
    }
    departure {
      delay: 134
      time: 1744181824
      uncertainty: 0
    }
  }
  stop_time_update {
    stop_sequence: 72
    stop_id: "9022001050366002"
    arrival {
      delay: 110
      time: 1744181930
      uncertainty: 0
    }
    departure {
      delay: 129
      time: 1744181949
      uncertainty: 0
    }
  }
  stop_time_update {
    stop_sequence: 73
    stop_id: "9022001051554002"
    arrival {
      delay: -66
      time: 1744182164
      uncertainty: 0
    }
    departure {
      delay: -66
      time: 1744182164
      uncertainty: 0
    }
  }
  stop_time_update {
    stop_sequence: 74
    stop_id: "9022001060301004"


In [7]:
rows = []

for e in feed.entity:
    if not e.HasField("trip_update"):
        continue

    tu = e.trip_update

    tr = tu.trip
    
    for stu in tu.stop_time_update:
        row = {
            "entity_id": e.id,
            "trip_id": tr.trip_id,
            "route_id": tr.route_id,
            "start_date": tr.start_date,
            "schedule_relationship": tr.schedule_relationship,
            "vehicle_id": tu.vehicle.id if tu.HasField("vehicle") else None,

            "stop_sequence": stu.stop_sequence,
            "stop_id": stu.stop_id,

            "stop_arrival_delay": stu.arrival.delay if stu.HasField("arrival") else None,
            "stop_arrival_time": stu.arrival.time if stu.HasField("arrival") else None,

            "departure_delay": stu.departure.delay if stu.HasField("departure") else None,
            "departure_time": stu.departure.time if stu.HasField("departure") else None,

            "timestamp": tu.timestamp if tu.timestamp else None
        }
        rows.append(row)


df = pd.DataFrame(rows)

In [8]:
df["stop_arrival_time"] = pd.to_datetime(df["stop_arrival_time"], unit="s", utc=True)
df["departure_time"] = pd.to_datetime(df["departure_time"], unit="s", utc=True)
df["timestamp"] = pd.to_datetime(df["timestamp"], unit="s", utc=True)
df["start_date"] = pd.to_datetime(df["start_date"], unit="s", utc=True)

df.head(10)
#FAIRE LES COLONNE DE DATER EN DATE LA J'AI UN PROBLEME AVEC LA DATE

/var/folders/xs/9pw_49kx273dmym0qk_0l_s00000gn/T/ipykernel_6771/2665421134.py:4: FutureWarning: The behavior of 'to_datetime' with 'unit' when parsing strings is deprecated. In a future version, strings will be parsed as datetime strings, matching the behavior without a 'unit'. To retain the old behavior, explicitly cast ints or floats to numeric type before calling to_datetime.
  df["start_date"] = pd.to_datetime(df["start_date"], unit="s", utc=True)


entity_id            trip_id route_id                start_date  \
0  14010516766425338  14010000664756938          1970-08-23 09:06:49+00:00   
1  14010516766425338  14010000664756938          1970-08-23 09:06:49+00:00   
2  14010516766425338  14010000664756938          1970-08-23 09:06:49+00:00   
3  14010516766425338  14010000664756938          1970-08-23 09:06:49+00:00   
4  14010516766425338  14010000664756938          1970-08-23 09:06:49+00:00   
5  14010516766425338  14010000664756938          1970-08-23 09:06:49+00:00   
6  14010516766425338  14010000664756938          1970-08-23 09:06:49+00:00   
7  14010516479399292  14010000668237873          1970-08-23 09:06:49+00:00   
8  14010516900582529  14010000684355399          1970-08-23 09:06:49+00:00   
9  14010516900582529  14010000684355399          1970-08-23 09:06:49+00:00   

   schedule_relationship        vehicle_id  stop_sequence           stop_id  \
0                      0  9031001004505106             71  9022001060014001   
1                      0  9031001004505106             72  9022001050366002   
2                      0  9031001004505106             73  9022001051554002   
3                      0  9031001004505106             74  9022001060301004   
4                      0  9031001004505106             75  9022001069011002   
5                      0  9031001004505106             76  9022001069009002   
6                      0  9031001004505106             77  9022001060080001   
7                      0  9031001004002216             25  9022001005007002   
8                      0  9031001004302315             21  9022001006231001   
9                      0  9031001004302315             22  9022001006241001   

   stop_arrival_delay         stop_arrival_time  departure_delay  \
0               120.0 2025-04-09 06:56:50+00:00            134.0   
1               110.0 2025-04-09 06:58:50+00:00            129.0   
2               -66.0 2025-04-09 07:02:44+00:00            -66.0   
3              -116.0 2025-04-09 07:03:29+00:00            -98.0   
4              -127.0 2025-04-09 07:04:58+00:00           -127.0   
5              -146.0 2025-04-09 07:05:53+00:00           -146.0   
6              -324.0 2025-04-09 07:09:36+00:00           -322.0   
7                86.0 2025-04-09 07:05:26+00:00             86.0   
8               280.0 2025-04-09 06:56:40+00:00            294.0   
9               207.0 2025-04-09 06:59:27+00:00            274.0   

             departure_time                 timestamp  
0 2025-04-09 06:57:04+00:00 2025-04-09 07:06:08+00:00  
1 2025-04-09 06:59:09+00:00 2025-04-09 07:06:08+00:00  
2 2025-04-09 07:02:44+00:00 2025-04-09 07:06:08+00:00  
3 2025-04-09 07:03:47+00:00 2025-04-09 07:06:08+00:00  
4 2025-04-09 07:04:58+00:00 2025-04-09 07:06:08+00:00  
5 2025-04-09 07:05:53+00:00 2025-04-09 07:06:08+00:00  
6 2025-04-09 07:09:38+00:00 2025-04-09 07:06:08+00:00  
7 2025-04-09 07:05:26+00:00 2025-04-09 07:05:06+00:00  
8 2025-04-09 06:57:54+00:00 2025-04-09 07:01:46+00:00  
9 2025-04-09 07:00:34+00:00 2025-04-09 07:01:46+00:00

In [9]:
df[df['trip_id'].notnull()]

entity_id            trip_id route_id  \
0      14010516766425338  14010000664756938            
1      14010516766425338  14010000664756938            
2      14010516766425338  14010000664756938            
3      14010516766425338  14010000664756938            
4      14010516766425338  14010000664756938            
...                  ...                ...      ...   
20511  14010516552820808  14010000670834912            
20512  14010516552820808  14010000670834912            
20513  14010516552820808  14010000670834912            
20514  14010516552820808  14010000670834912            
20515  14010516552820808  14010000670834912            

                     start_date  schedule_relationship        vehicle_id  \
0     1970-08-23 09:06:49+00:00                      0  9031001004505106   
1     1970-08-23 09:06:49+00:00                      0  9031001004505106   
2     1970-08-23 09:06:49+00:00                      0  9031001004505106   
3     1970-08-23 09:06:49+00:00                      0  9031001004505106   
4     1970-08-23 09:06:49+00:00                      0  9031001004505106   
...                         ...                    ...               ...   
20511 1970-08-23 09:06:49+00:00                      0  9031001004505524   
20512 1970-08-23 09:06:49+00:00                      0  9031001004505524   
20513 1970-08-23 09:06:49+00:00                      0  9031001004505524   
20514 1970-08-23 09:06:49+00:00                      0  9031001004505524   
20515 1970-08-23 09:06:49+00:00                      0  9031001004505524   

       stop_sequence           stop_id  stop_arrival_delay  \
0                 71  9022001060014001               120.0   
1                 72  9022001050366002               110.0   
2                 73  9022001051554002               -66.0   
3                 74  9022001060301004              -116.0   
4                 75  9022001069011002              -127.0   
...              ...               ...                 ...   
20511             18  9022001062213001                 0.0   
20512             19  9022001062227001                 0.0   
20513             20  9022001062228002                 0.0   
20514             21  9022001062226002                 0.0   
20515             22  9022001062233001                 0.0   

              stop_arrival_time  departure_delay            departure_time  \
0     2025-04-09 06:56:50+00:00            134.0 2025-04-09 06:57:04+00:00   
1     2025-04-09 06:58:50+00:00            129.0 2025-04-09 06:59:09+00:00   
2     2025-04-09 07:02:44+00:00            -66.0 2025-04-09 07:02:44+00:00   
3     2025-04-09 07:03:29+00:00            -98.0 2025-04-09 07:03:47+00:00   
4     2025-04-09 07:04:58+00:00           -127.0 2025-04-09 07:04:58+00:00   
...                         ...              ...                       ...   
20511 2025-04-09 07:31:00+00:00              0.0 2025-04-09 07:31:00+00:00   
20512 2025-04-09 07:33:23+00:00              0.0 2025-04-09 07:33:23+00:00   
20513 2025-04-09 07:34:41+00:00              0.0 2025-04-09 07:34:41+00:00   
20514 2025-04-09 07:36:51+00:00              0.0 2025-04-09 07:36:51+00:00   
20515 2025-04-09 07:40:00+00:00              0.0 2025-04-09 07:40:00+00:00   

                      timestamp  
0     2025-04-09 07:06:08+00:00  
1     2025-04-09 07:06:08+00:00  
2     2025-04-09 07:06:08+00:00  
3     2025-04-09 07:06:08+00:00  
4     2025-04-09 07:06:08+00:00  
...                         ...  
20511 2025-04-09 07:06:02+00:00  
20512 2025-04-09 07:06:02+00:00  
20513 2025-04-09 07:06:02+00:00  
20514 2025-04-09 07:06:02+00:00  
20515 2025-04-09 07:06:02+00:00  

[20516 rows x 13 columns]

In [10]:
len(df["trip_id"].unique())

1263

In [11]:
df_with_trip_id = df[df["trip_id"] != ""]
df_with_trip_id

entity_id            trip_id route_id  \
0      14010516766425338  14010000664756938            
1      14010516766425338  14010000664756938            
2      14010516766425338  14010000664756938            
3      14010516766425338  14010000664756938            
4      14010516766425338  14010000664756938            
...                  ...                ...      ...   
20511  14010516552820808  14010000670834912            
20512  14010516552820808  14010000670834912            
20513  14010516552820808  14010000670834912            
20514  14010516552820808  14010000670834912            
20515  14010516552820808  14010000670834912            

                     start_date  schedule_relationship        vehicle_id  \
0     1970-08-23 09:06:49+00:00                      0  9031001004505106   
1     1970-08-23 09:06:49+00:00                      0  9031001004505106   
2     1970-08-23 09:06:49+00:00                      0  9031001004505106   
3     1970-08-23 09:06:49+00:00                      0  9031001004505106   
4     1970-08-23 09:06:49+00:00                      0  9031001004505106   
...                         ...                    ...               ...   
20511 1970-08-23 09:06:49+00:00                      0  9031001004505524   
20512 1970-08-23 09:06:49+00:00                      0  9031001004505524   
20513 1970-08-23 09:06:49+00:00                      0  9031001004505524   
20514 1970-08-23 09:06:49+00:00                      0  9031001004505524   
20515 1970-08-23 09:06:49+00:00                      0  9031001004505524   

       stop_sequence           stop_id  stop_arrival_delay  \
0                 71  9022001060014001               120.0   
1                 72  9022001050366002               110.0   
2                 73  9022001051554002               -66.0   
3                 74  9022001060301004              -116.0   
4                 75  9022001069011002              -127.0   
...              ...               ...                 ...   
20511             18  9022001062213001                 0.0   
20512             19  9022001062227001                 0.0   
20513             20  9022001062228002                 0.0   
20514             21  9022001062226002                 0.0   
20515             22  9022001062233001                 0.0   

              stop_arrival_time  departure_delay            departure_time  \
0     2025-04-09 06:56:50+00:00            134.0 2025-04-09 06:57:04+00:00   
1     2025-04-09 06:58:50+00:00            129.0 2025-04-09 06:59:09+00:00   
2     2025-04-09 07:02:44+00:00            -66.0 2025-04-09 07:02:44+00:00   
3     2025-04-09 07:03:29+00:00            -98.0 2025-04-09 07:03:47+00:00   
4     2025-04-09 07:04:58+00:00           -127.0 2025-04-09 07:04:58+00:00   
...                         ...              ...                       ...   
20511 2025-04-09 07:31:00+00:00              0.0 2025-04-09 07:31:00+00:00   
20512 2025-04-09 07:33:23+00:00              0.0 2025-04-09 07:33:23+00:00   
20513 2025-04-09 07:34:41+00:00              0.0 2025-04-09 07:34:41+00:00   
20514 2025-04-09 07:36:51+00:00              0.0 2025-04-09 07:36:51+00:00   
20515 2025-04-09 07:40:00+00:00              0.0 2025-04-09 07:40:00+00:00   

                      timestamp  
0     2025-04-09 07:06:08+00:00  
1     2025-04-09 07:06:08+00:00  
2     2025-04-09 07:06:08+00:00  
3     2025-04-09 07:06:08+00:00  
4     2025-04-09 07:06:08+00:00  
...                         ...  
20511 2025-04-09 07:06:02+00:00  
20512 2025-04-09 07:06:02+00:00  
20513 2025-04-09 07:06:02+00:00  
20514 2025-04-09 07:06:02+00:00  
20515 2025-04-09 07:06:02+00:00  

[20398 rows x 13 columns]

In [12]:
len(df_with_trip_id["trip_id"].unique())

1262

In [13]:
len(df["route_id"].unique())

2

In [14]:
df["route_id"].unique()

array(['', '9011001001800000'], dtype=object)

In [15]:
df_with_route_id = df[df["route_id"] != ""]
df_with_route_id

entity_id trip_id          route_id                start_date  \
17   14050001802168556          9011001001800000 1970-08-23 09:06:49+00:00   
18   14050001802168556          9011001001800000 1970-08-23 09:06:49+00:00   
19   14050001802168556          9011001001800000 1970-08-23 09:06:49+00:00   
20   14050001802168556          9011001001800000 1970-08-23 09:06:49+00:00   
21   14050001802168556          9011001001800000 1970-08-23 09:06:49+00:00   
..                 ...     ...               ...                       ...   
130  14050001802168556          9011001001800000 1970-08-23 09:06:49+00:00   
131  14050001802168556          9011001001800000 1970-08-23 09:06:49+00:00   
132  14050001802168556          9011001001800000 1970-08-23 09:06:49+00:00   
133  14050001802168556          9011001001800000 1970-08-23 09:06:49+00:00   
134  14050001802168556          9011001001800000 1970-08-23 09:06:49+00:00   

     schedule_relationship        vehicle_id  stop_sequence           stop_id  \
17                       3  9031001002500110              1  9022001001951002   
18                       3  9031001002500110              2  9022001001951001   
19                       3  9031001002500110              3  9022001001941001   
20                       3  9031001002500110              4  9022001001941002   
21                       3  9031001002500110              5  9022001001931001   
..                     ...               ...            ...               ...   
130                      3  9031001002500110            114  9022001001311002   
131                      3  9031001002500110            115  9022001001321001   
132                      3  9031001002500110            116  9022001001321002   
133                      3  9031001002500110            117  9022001001331001   
134                      3  9031001002500110            118  9022001001331002   

     stop_arrival_delay         stop_arrival_time  departure_delay  \
17                  0.0 2025-04-09 05:36:02+00:00              0.0   
18                  0.0 2025-04-09 05:36:02+00:00              0.0   
19                  0.0 2025-04-09 05:36:02+00:00              0.0   
20                  0.0 2025-04-09 05:36:02+00:00              0.0   
21                  0.0 2025-04-09 05:36:02+00:00              0.0   
..                  ...                       ...              ...   
130                 0.0 2025-04-09 05:36:02+00:00              0.0   
131                 0.0 2025-04-09 05:36:02+00:00              0.0   
132                 0.0 2025-04-09 05:36:02+00:00              0.0   
133                 0.0 2025-04-09 05:36:02+00:00              0.0   
134                 0.0 2025-04-09 07:36:02+00:00              0.0   

               departure_time                 timestamp  
17  2025-04-09 05:36:02+00:00 2025-04-09 05:36:06+00:00  
18  2025-04-09 05:36:02+00:00 2025-04-09 05:36:06+00:00  
19  2025-04-09 05:36:02+00:00 2025-04-09 05:36:06+00:00  
20  2025-04-09 05:36:02+00:00 2025-04-09 05:36:06+00:00  
21  2025-04-09 05:36:02+00:00 2025-04-09 05:36:06+00:00  
..                        ...                       ...  
130 2025-04-09 05:36:02+00:00 2025-04-09 05:36:06+00:00  
131 2025-04-09 05:36:02+00:00 2025-04-09 05:36:06+00:00  
132 2025-04-09 05:36:02+00:00 2025-04-09 05:36:06+00:00  
133 2025-04-09 05:36:02+00:00 2025-04-09 05:36:06+00:00  
134 2025-04-09 07:36:02+00:00 2025-04-09 05:36:06+00:00  

[118 rows x 13 columns]

In [16]:
df_with_route_id["route_id"].unique()

array(['9011001001800000'], dtype=object)